# Get Wendy's locations

#### Load Python tools and Jupyter config

In [1]:
%load_ext lab_black

In [2]:
import json
import requests
import pandas as pd
import altair as alt
import geopandas as gpd
from tqdm.notebook import tqdm, trange
from vega_datasets import data
from time import sleep
from random import randint

In [3]:
pd.options.display.max_rows = 1000
pd.options.display.max_columns = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [4]:
place = "Wendys"

#### Request data from evenly distributed large ZIP Codes in the US

In [5]:
responses = []

for zip in [
    "90001",
    "10001",
    "78015",
    "32301",
    "98101",
    "28105",
    "60007",
    "85641",
    "37011",
]:

    headers = {
        "authority": "api.app.prd.wendys.digital",
        "accept": "application/json",
        "content-type": "application/json",
        "origin": "https://order.wendys.com",
        "referer": "https://order.wendys.com/",
        "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/121.0.0.0 Safari/537.36",
    }

    response = requests.get(
        f"https://api.app.prd.wendys.digital/web-client-gateway/LocationServices/rest/nearbyLocations?&lang=en&cntry=US&sourceCode=ORDER.WENDYS&version=23.0.1&address={zip}&limit=2000&radius=2000",
        headers=headers,
    )
    print(
        f"Recieved a {response.status_code} for the {zip} zip code.",
    )
    dfs = pd.DataFrame(response.json()["data"])

    responses.append(dfs)

Recieved a 200 for the 90001 zip code.
Recieved a 200 for the 10001 zip code.
Recieved a 200 for the 78015 zip code.
Recieved a 200 for the 32301 zip code.
Recieved a 200 for the 98101 zip code.
Recieved a 200 for the 28105 zip code.
Recieved a 200 for the 60007 zip code.
Recieved a 200 for the 85641 zip code.
Recieved a 200 for the 37011 zip code.


#### Into one big dataframe

In [6]:
df_src = pd.concat(responses).drop_duplicates(subset="name").reset_index()

#### How many?

In [7]:
len(df_src)

6160

#### Clean up the dataframe

In [8]:
df = (
    df_src[
        [
            "id",
            "address1",
            "city",
            "state",
            "postal",
            "lat",
            "lng",
            "phone",
            "storeStatusCode",
            "timezoneId",
        ]
    ]
    .rename(
        columns={
            "address1": "address",
            "postal": "zip",
            "lat": "latitude",
            "lng": "longitude",
        }
    )
    .copy()
)

#### The result

In [9]:
df.head()

id                       address         city state    zip    latitude  \
0  12293              3297 TWEEDY BLVD   SOUTH GATE    CA  90280   33.945153   
1  12294             4148 FLORENCE AVE         BELL    CA  90201   33.970763   
2  12134           8810 S GARFIELD AVE   SOUTH GATE    CA  90280   33.950545   
3   9836         3504 W. CENTURY BLVD.    INGLEWOOD    CA  90303    33.94482   
4  13151  800 S FIGUEROA ST, SUITE 103  LOS ANGELES    CA  90017  34.0478103   

      longitude       phone storeStatusCode  timezoneId  
0   -118.214226  3235374745              OP  US/Pacific  
1   -118.194282  3235374507              OP  US/Pacific  
2   -118.164457  5627760204              OP  US/Pacific  
3    -118.33339  3106735382              OP  US/Pacific  
4  -118.2612876  2134441888              OP  US/Pacific

---

## Geography

#### Make it a geodataframe

In [10]:
df_geo = df.copy()

In [11]:
gdf = gpd.GeoDataFrame(
    df_geo, geometry=gpd.points_from_xy(df_geo.longitude, df_geo.latitude)
)

In [12]:
locations_gdf = gdf.set_crs("EPSG:4326").copy()

---

## Maps

#### US states background

In [13]:
background = (
    alt.Chart(alt.topo_feature(data.us_10m.url, feature="states"))
    .mark_geoshape(fill="#e9e9e9", stroke="white")
    .properties(width=800, height=500, title=f"{place} locations")
    .project("albersUsa")
)

#### Location points map

In [14]:
points = (
    alt.Chart(gdf)
    .mark_circle(size=3, color="#e2203d")
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
    )
)

point_map = background + points
point_map.configure_view(stroke=None)

alt.LayerChart(...)

#### Location proportional symbols map

In [15]:
symbols = (
    alt.Chart(gdf)
    .transform_aggregate(
        latitude="mean(latitude)",
        longitude="mean(longitude)",
        count="count()",
        groupby=["state"],
    )
    .mark_circle()
    .encode(
        longitude="longitude:Q",
        latitude="latitude:Q",
        size=alt.Size("count:Q", title="Count by state"),
        color=alt.value("#e2203d"),
        tooltip=["state:N", "count:Q"],
    )
    .properties(title=f"Number of {place} in US, by average lon/lat of locations")
)

symbol_map = background + symbols
symbol_map.configure_view(stroke=None)

alt.LayerChart(...)

---

## Exports

#### JSON

In [16]:
df.to_json(f"data/processed/{place.lower()}_locations.json", indent=4, orient="records")

#### CSV

In [17]:
df.to_csv(f"data/processed/{place.lower()}_locations.csv", index=False)

#### GeoJSON

In [18]:
locations_gdf.to_file(
    f"data/processed/{place.lower()}_locations.geojson", driver="GeoJSON"
)